In [1]:
import pandas as pd
import pandas_profiling
import numpy as np
import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split,KFold
from catboost import CatBoostRegressor
from sklearn.ensemble import RandomForestRegressor, ExtraTreesRegressor,GradientBoostingRegressor
from sklearn.linear_model import LinearRegression

import warnings
warnings.filterwarnings("ignore")

%matplotlib inline
pd.set_option('display.max_columns', 50)

In [2]:
RandomSeed = 32 # фиксируем рандом

In [3]:
def mape(y_true, y_pred):
    """Функция вычисления метрики"""
    return np.mean(np.abs((y_pred-y_true)/y_true))    

In [4]:
# Подгрузим наши данные
df_train = pd.read_csv('data.csv')
df_test = pd.read_csv('test.csv')
df_sub = pd.read_csv('sample_submission.csv')

# 1.Подготовка данныз и разведочный анализ

In [5]:
# Для начала посмотрим на наши тестовые данные. Есть ли там пропуски
df_test.isnull().sum()

bodyType                    0
brand                       0
car_url                     0
color                       0
complectation_dict      28268
description                 0
engineDisplacement          0
enginePower                 0
equipment_dict           9996
fuelType                    0
image                       0
mileage                     0
modelDate                   0
model_info                  0
model_name                  0
name                        0
numberOfDoors               0
parsing_unixtime            0
priceCurrency               0
productionDate              0
sell_id                     0
super_gen                   0
vehicleConfiguration        0
vehicleTransmission         0
vendor                      0
Владельцы                   0
Владение                22691
ПТС                         1
Привод                      0
Руль                        0
Состояние                   0
Таможня                     0
dtype: int64

Избавимся от столбцов с пропусками, в столбце "ПТС" пропуск заменим на моду. Также избавися от столбцов которые пока не можем использовать или в них информация повторяет уже имеющиеся в других столбцах.

In [6]:
df_test.drop(['complectation_dict','equipment_dict','Владение','description','model_info',
             'name','vendor','Владение'],axis=1,inplace=True) # удаляем столбцы

df_test['ПТС'].fillna('Оригинал',inplace=True)  # заменим пустое значение 

In [7]:
# Воспользуемся удобной библиотекой pandas_profiling
pandas_profiling.ProfileReport(df_test)

Как видим есть столбцы которые не меняют свои значения, такие  как: priceCurrency, Состояние, Таможня. Не знаю на сколько это правильно, но думаю в обучающей выборке надо оставить только те строки которые соответсвуют значениямтестовой в этих столбцах. Дальше просто удаляем эти столбцы. Модель конечно после этого не сможет определять сотояние автомобиля и учитывать его при предсказании цены. Но в рамках конкретной задачи с этой тестовой выборкой это и не нужно.

In [8]:
df_test.drop(['priceCurrency','Состояние','Таможня'], axis=1,inplace=True)
df_train = df_train.query('Состояние == "Не требует ремонта" & Таможня == "Растаможен"')
df_train.drop(['priceCurrency','Состояние','Таможня'], axis=1,inplace=True)

Пометим наши обучающую и тестовую выборки и объеденим их в один датасет.

In [9]:
df_train['train'] = 1 # обучающая выборка
df_test['train'] = 0 # тестовая выборка
data = pd.concat([df_train,df_test],ignore_index=True)

Пройдемся по признакам и проверим правильность значений. Также попробуем кое где сократить количество значений.   

In [10]:
# bodyType
data.bodyType.value_counts() 

седан                      60600
внедорожник 5 дв.          58431
хэтчбек 5 дв.              11365
лифтбек                     9372
универсал 5 дв.             6806
минивэн                     5207
купе                        3224
компактвэн                  3146
хэтчбек 3 дв.               1870
пикап двойная кабина        1499
купе-хардтоп                 658
фургон                       653
внедорожник 3 дв.            570
родстер                      377
кабриолет                    332
седан-хардтоп                216
микровэн                     118
пикап одинарная кабина        37
седан 2 дв.                   28
пикап полуторная кабина       27
внедорожник открытый          11
лимузин                       10
тарга                          3
фастбек                        1
Name: bodyType, dtype: int64

Оставлю самые популярные кузова остальные обозначу как 'other'

In [11]:
bodyT = ['седан','внедорожник','хэтчбек','лифтбек','универсал','минивэн','купе','компактвэн']
data.bodyType = data.bodyType.apply(lambda x: x.replace(' 5 дв.','')) # удалим окончание 5 дв
data.bodyType = data.bodyType.apply(lambda x: x.replace(' 3 дв.','')) # удалим окончание 3 дв
data.bodyType = data.bodyType.apply(lambda x: x if x in bodyT else 'other') # кузова не из списка заменим на other
data.bodyType.value_counts() 

седан          60600
внедорожник    59001
хэтчбек        13235
лифтбек         9372
универсал       6806
минивэн         5207
other           3970
купе            3224
компактвэн      3146
Name: bodyType, dtype: int64

In [12]:
# brand
data.brand.value_counts() 

TOYOTA        24450
VOLKSWAGEN    22420
NISSAN        21714
MERCEDES      20676
BMW           19638
MITSUBISHI    13258
AUDI          13187
SKODA         11178
HONDA          6117
VOLVO          4826
LEXUS          4232
INFINITI       2865
Name: brand, dtype: int64

Тут все в порядке

In [13]:
# car_url
# от этого столбца избавимся так как он не несет какой то нужной информации
data.drop(['car_url'],axis=1,inplace=True)

In [14]:
# color
data.color.value_counts() 

чёрный         47557
белый          34183
серый          21448
серебристый    19524
синий          14839
красный         7194
коричневый      6212
зелёный         4503
бежевый         2742
голубой         1884
золотистый      1140
пурпурный       1129
фиолетовый       940
жёлтый           701
оранжевый        500
розовый           65
Name: color, dtype: int64

Здесь тоже все в порядке

In [15]:
# engineDisplacement
data.engineDisplacement.value_counts() 

2.0 LTR    36583
1.6 LTR    23895
3.0 LTR    17541
1.8 LTR    14813
2.5 LTR    11309
1.4 LTR     8031
2.4 LTR     7088
3.5 LTR     6835
1.5 LTR     5492
1.2 LTR     2503
1.3 LTR     2376
2.8 LTR     2002
4.5 LTR     1727
4.4 LTR     1705
2.2 LTR     1638
3.2 LTR     1594
4.7 LTR     1551
4.0 LTR     1506
5.5 LTR     1429
2.1 LTR     1275
2.3 LTR     1130
2.7 LTR     1113
1.9 LTR     1093
4.2 LTR      965
3.6 LTR      872
3.7 LTR      776
1.0 LTR      716
5.7 LTR      682
5.6 LTR      679
5.0 LTR      647
2.9 LTR      584
4.6 LTR      550
 LTR         535
0.7 LTR      519
2.6 LTR      364
1.7 LTR      329
4.8 LTR      314
3.1 LTR      269
3.3 LTR      259
3.8 LTR      236
3.4 LTR      163
6.0 LTR      161
4.3 LTR      156
6.2 LTR      135
5.4 LTR      127
4.1 LTR      123
5.2 LTR       29
5.8 LTR       28
5.9 LTR       24
6.6 LTR       23
1.1 LTR       23
6.3 LTR       19
4.9 LTR       15
3.9 LTR        8
0.6 LTR        1
5.3 LTR        1
Name: engineDisplacement, dtype: int64

Здесь надо избавиться от окончания LTR, заполнить пустые значения, а также перевести данные в численный формат.

In [16]:
data.engineDisplacement = data.engineDisplacement.apply(lambda x: x.replace(' LTR','')) # избавляемся от окончаний
data.engineDisplacement = data.engineDisplacement.replace(r'^\s*$', np.nan, regex=True)# пропуски в виде пробелов заменим на nan
data.engineDisplacement.fillna('2.0',inplace=True) # пропуски заменим на моду 2.0
data.engineDisplacement = data.engineDisplacement.astype(np.float64) # изменим тип данных на float64

In [17]:
# enginePower
data.enginePower.value_counts()

150 N12    9460
249 N12    8550
110 N12    6027
105 N12    4962
170 N12    4467
           ... 
47 N12        1
134 N12       1
153 N12       1
63 N12        1
311 N12       1
Name: enginePower, Length: 348, dtype: int64

В этом столбце проведем те же операции что и в предыдущем

In [18]:
data.enginePower = data.enginePower.apply(lambda x: x.replace(' N12','')) # избавляемся от окончаний
data.enginePower = data.enginePower.astype(int) # изменим тип данных на float64

In [19]:
# fuelType
data.fuelType.value_counts()

бензин     133197
дизель      28354
гибрид       2437
электро       535
газ            38
Name: fuelType, dtype: int64

Здесь все хорошо

In [20]:
# image
# от этого столбца избавляемся за ненадобностью
data.drop(['image'],axis=1,inplace=True)

In [21]:
# mileage
data.mileage.value_counts()

300 000 км    2121
200 000 км    2076
250 000 км    1723
150 000 км    1365
180 000 км    1260
              ... 
163 886 км       1
122 768 км       1
166502           1
223 568 км       1
79 504 км        1
Name: mileage, Length: 43206, dtype: int64

Избавимся от окончаний и переведем в численный формат

In [22]:
data.mileage = data.mileage.astype(str)
data.mileage = data.mileage.apply(lambda x: x.replace(' км','')) # избавляемся от окончаний
data.mileage = data.mileage.apply(lambda x: x.replace(' ','')) # избавляемся от окончаний
data.mileage = data.mileage.astype(int) # изменим тип данных на int

In [23]:
# modelDate
data.modelDate.value_counts()

2010    10964
2013    10204
2014    10166
2011     9572
2012     9025
        ...  
1967        2
1952        1
1961        1
1969        1
1904        1
Name: modelDate, Length: 72, dtype: int64

Здесь все вроде в порядке

In [24]:
# model_name
data.model_name.value_counts()

Octavia     4029
Polo        3861
5 серии     3549
E-Класс     3370
Passat      3188
            ... 
VERSO_S        1
POLO_GTI       1
ID.4           1
X_KLASSE       1
GOLF_R32       1
Name: model_name, Length: 1084, dtype: int64

Здесь тоже оставляем все как есть

In [25]:
# numberOfDoors
display(data.numberOfDoors.value_counts())
data.query('numberOfDoors==0')

5    91477
4    65635
2     4723
3     2725
0        1
Name: numberOfDoors, dtype: int64

bodyType     brand  color  engineDisplacement  enginePower fuelType  \
146819    other  MERCEDES  белый                 5.3           32   бензин   

        mileage  modelDate model_name  numberOfDoors  parsing_unixtime  \
146819    48000       1904    SIMPLEX              0        1603245843   

        productionDate     sell_id  \
146819            1904  1093802104   

                                                super_gen  \
146819  {"id":"21743990","displacement":5322,"engine_t...   

         vehicleConfiguration vehicleTransmission   Владельцы       ПТС  \
146819  CABRIO MECHANICAL 5.3        механическая  1 владелец  Оригинал   

        Привод    Руль  price  train  
146819  задний  Правый    NaN      0

О, здесь есть интересный экземпляр. Вообще без дверей. Это не ошибка, автомобиль действительно без дверей. Чтоб не путать нашу модель, заменим значение на 2 двери. Все таки в машину можно попасть с двух сторон.

In [26]:
data.loc[137655,'numberOfDoors'] = 2

In [27]:
# parsing_unixtime
# Дата когда был произведен парсинг. Не думаю что эта информация как то должна влиять на цену авто. Удаляем столбец.
data.drop(['parsing_unixtime'],axis=1,inplace=True)

In [28]:
# productionDate
data.productionDate.unique()

array([1998, 1991, 1990, 1995, 1987, 1997, 2001, 2002, 2005, 1992, 2011,
       2000, 2003, 1999, 1996, 2004, 1993, 1989, 1983, 1986, 2006, 1988,
       2013, 2007, 1994, 1985, 2008, 1979, 2009, 1984, 1977, 1982, 1981,
       2010, 1980, 2012, 2014, 2015, 2016, 2018, 2017, 2019, 2020, 2021,
       1978, 1976, 1949, 1951, 1946, 1952, 1975, 1971, 1947, 1953, 1968,
       1942, 1959, 1937, 1974, 1973, 1972, 1939, 1965, 1935, 1970, 1969,
       1966, 1960, 1961, 1963, 1958, 1950, 1938, 1936, 1904, 1967, 1957,
       1948], dtype=int64)

Здесь все выглядит хорошо

In [29]:
# super_gen
# Дополнительная информация по авто. Пока уберу этот столбец, если понадобится буду с ним разбираться отдельно.
data.drop(['super_gen'],axis=1,inplace=True)

In [30]:
# vehicleConfiguration
# столбец содержит информацию которая уже присутствует в других столбцах. Убираем его.
data.drop(['vehicleConfiguration'],axis=1,inplace=True)

In [31]:
# vehicleTransmission тип коробки
data.vehicleTransmission.value_counts()

автоматическая      90673
механическая        37295
вариатор            20378
роботизированная    16215
Name: vehicleTransmission, dtype: int64

Здесь тоже все хорошо.

In [32]:
# Владельцы
data['Владельцы'].value_counts()

3 или более    83201
1 владелец     33307
2 владельца    29324
1 владелец      9459
2 владельца     9270
Name: Владельцы, dtype: int64

По сути у нас тут 3 категории: 1, 2, 3 и более. Так и заменим их на 1,2,3

In [33]:
data['Владельцы'] = data['Владельцы'].apply(lambda x: x[0])

In [34]:
# ПТС
data['ПТС'].value_counts()

Оригинал    137409
Дубликат     27152
Name: ПТС, dtype: int64

Оставляем как есть

In [35]:
# Привод
data['Привод'].value_counts()

передний    74861
полный      69173
задний      20527
Name: Привод, dtype: int64

Оставляем

In [36]:
# Руль
data['Руль'].value_counts()

Левый     148029
Правый     16532
Name: Руль, dtype: int64

Оставляем

In [37]:
# еще раз воспользуемся библиотекой pandas_profiling
pandas_profiling.ProfileReport(data)

Что мы видим по анализу:
1. после всех преобразований появились дубликаты
2. признаки: engineDisplacement, enginePower, mileage, price имеют распределение сдвинутое в право. Позже прологорифмируем эти признаки что придать им вид более нормального распределения
3. признаки: modelDate и productionDate тоже кажутся сдвинутыми, но на самом деле там просто выброс за счет а авто 1904 года из тестовой выборки, так что эти признаки не трогаем
4. признак mileage имеет выбросы, подожмем его значения 
5. Видна довольно сильная корреляция между признаками: 
- engineDisplacement и enginePower что логично чем больше объем двигателя тем больше у него мощность
- modelDate и productionDate тоже все объяснимо чем старше модель тем более раннее ее поколение  
- productionDate и mileage тоже все понятно, чем старше модель тем больше у нее пробег 

Все эти признаки хорошо коррелируют с целевой переменной так что их оставим. А вот корреляция между целевой переменной и признаком NumberOfDoors очень низкая. Думаю этот признак будет иметь очень маленькую значимость и думаю его стоит убрать. 

====

In [38]:
data.query('train==1').drop_duplicates(inplace=True) # Удаляем дубликаты из тренировочной выборки

In [39]:
# логарифмируем engineDisplacement
data.engineDisplacement = np.log(data.engineDisplacement)

In [40]:
# mileage 
# все что больше 500 тыс км поджимаем и потом логорифмируем
data.mileage= data.mileage.apply(lambda x: 500000 if x>500000 else x)
data.mileage = np.log(data.mileage)

In [41]:
# логарифмируем enginePower
data.enginePower = np.log(data.enginePower)

In [42]:
# выберем категориальные и бинарные признаки
cat_cols = ['bodyType','brand','color','fuelType','model_name','vehicleTransmission',
           'Владельцы','ПТС','Привод','Руль']

In [43]:
# разобъем категареальные признаки
data = pd.get_dummies(data, columns=cat_cols, dummy_na=False)

# 2. Построение моделей

In [44]:
# Готовим данные и разбиваем на тренировочную и валидационные выборки
X = data.query('train==1').drop(['sell_id','price','train','numberOfDoors'],axis=1)
Y = data.query('train==1').price
X_sub = data.query('train==0').drop(['sell_id','price','train','numberOfDoors'],axis=1)

x_train,x_test,y_train,y_test = train_test_split(X, Y, test_size=0.20, random_state = RandomSeed)

Наиную модель не строил т.к. в baseline уже видел результат и понятно что надо получить не хуже
Проверял несколько моделей сначала на стандартных параметрах. Лучшие результаты показали CatBoost и RandomForest. В случайном лесу параметры пришлось подбирать вручную т.к. перебирать все по сетке оказалось слишком долго. Также не забываем про логарифмирование целевой переменной.

In [45]:
cat_boost = CatBoostRegressor(iterations = 5000,
                          random_seed = RandomSeed,
                          eval_metric='MAPE',
                          custom_metric=['R2', 'MAE'],
                          silent=True,
                         )
cat_boost.fit(x_train, np.log(y_train),
         eval_set=(x_test, np.log(y_test)),
         verbose_eval=0,
         use_best_model=True,)

predict = np.exp(cat_boost.predict(x_test))

# оцениваем точность
print(f"Точность модели по метрике MAPE: {(mape(y_test, predict))*100:0.2f}%")


Точность модели по метрике MAPE: 14.28%


In [46]:
RF= RandomForestRegressor(n_jobs=-1, random_state=RandomSeed, max_depth=25, n_estimators=1000)
RF.fit(x_train,np.log(y_train))
y_RF_pred=np.exp(RF.predict(x_test))

print(f"Точность модели по метрике MAPE: {(mape(y_test, y_RF_pred))*100:0.2f}%")

Точность модели по метрике MAPE: 13.91%


# 3. Готовим данные на отправку

In [47]:
predict_submission = np.exp(RF.predict(X_sub))
df_sub['price'] = predict_submission
# В связи с тем что тестовая выборка была сформирована некоторое время назад, то цены предсказаные моделью 
# могут быть смещены
# оказалось так и есть, судя по результатам с лидерборда цены в серднем поднялись
# методом перебора подобрал коэффициент 1,25 (возможно конечно что это просто подбивка под красивый ответ)
df_sub['price'] = df_sub['price']/1.25
df_sub.to_csv(f'submission.csv', index=False)
df_sub.head(10)

sell_id         price
0  1100575026  6.182318e+05
1  1100549428  9.368256e+05
2  1100658222  8.768520e+05
3  1100937408  8.967517e+05
4  1101037972  8.939974e+05
5  1100912634  7.083336e+05
6  1101228730  7.349988e+05
7  1100165896  4.277840e+05
8  1100768262  1.781008e+06
9  1101218501  8.436878e+05

Вывод: В проекте мы собрали себе датасет спарсив данные с сайта auto.ru. Очистили данные и провели разведочный анализ. Построили модель которая ошибается в среднем в пределах 15%. Что можно было еще сделать чтобы повысить результат:
- Спарсить больше данных
- добавить новые признаки
- попробовать использовать другие модели и более точно подобрать параметры

К сожалению чтобы все это реализавать нужно больше одной недели как отводится на проект. 

На кагле ник Vitalik, в лидерборде значение - 15,47280